In [1]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import plotly.express as px
import statistics as st

def get_df(day):
    file_name = f"./round-3-island-data-bottle/prices_round_3_day_{day}.csv"
    return pd.read_csv(file_name, sep=';')

def get_product(df, product):
    return df[df['product'] == product].copy()

def get_dfs():
    first_df = get_df(0)
    first_df['expiry'] = 7/252
    second_df = get_df(1)
    second_df['timestamp'] = second_df['timestamp'] + 1000000
    second_df['expiry'] = 6/252
    third_df = get_df(2)
    third_df['timestamp'] = third_df['timestamp'] + 2000000
    third_df['expiry'] = 5/252
    return pd.concat([first_df, second_df, third_df])

In [2]:
df = get_dfs()
df

day  timestamp                      product  bid_price_1  \
0         0          0  VOLCANIC_ROCK_VOUCHER_10500         99.0   
1         0          0                      DJEMBES      13493.0   
2         0          0                   CROISSANTS       4321.0   
3         0          0                         JAMS       6631.0   
4         0          0  VOLCANIC_ROCK_VOUCHER_10000        505.0   
...     ...        ...                          ...          ...   
139995    2    2999900               PICNIC_BASKET2      30073.0   
139996    2    2999900   VOLCANIC_ROCK_VOUCHER_9750        417.0   
139997    2    2999900               PICNIC_BASKET1      58422.0   
139998    2    2999900                   CROISSANTS       4241.0   
139999    2    2999900   VOLCANIC_ROCK_VOUCHER_9500        666.0   

        bid_volume_1  bid_price_2  bid_volume_2  bid_price_3  bid_volume_3  \
0               19.0          NaN           NaN          NaN           NaN   
1               72.0          NaN           NaN          NaN           NaN   
2              111.0          NaN           NaN          NaN           NaN   
3              210.0          NaN           NaN          NaN           NaN   
4               19.0          NaN           NaN          NaN           NaN   
...              ...          ...           ...          ...           ...   
139995           1.0      30072.0          39.0          NaN           NaN   
139996          20.0          NaN           NaN          NaN           NaN   
139997           1.0      58421.0          39.0          NaN           NaN   
139998         143.0          NaN           NaN          NaN           NaN   
139999          20.0          NaN           NaN          NaN           NaN   

        ask_price_1  ask_volume_1  ask_price_2  ask_volume_2  ask_price_3  \
0               100            19          NaN           NaN          NaN   
1             13494            72          NaN           NaN          NaN   
2              4322           111          NaN           NaN          NaN   
3              6633           210          NaN           NaN          NaN   
4               506            19          NaN           NaN          NaN   
...             ...           ...          ...           ...          ...   
139995        30078            20      30079.0          20.0          NaN   
139996          418            20          NaN           NaN          NaN   
139997        58432            20      58433.0          20.0          NaN   
139998         4242           143          NaN           NaN          NaN   
139999          667            20          NaN           NaN          NaN   

        ask_volume_3  mid_price  profit_and_loss    expiry  
0                NaN       99.5              0.0  0.027778  
1                NaN    13493.5              0.0  0.027778  
2                NaN     4321.5              0.0  0.027778  
3                NaN     6632.0              0.0  0.027778  
4                NaN      505.5              0.0  0.027778  
...              ...        ...              ...       ...  
139995           NaN    30075.5              0.0  0.019841  
139996           NaN      417.5              0.0  0.019841  
139997           NaN    58427.0              0.0  0.019841  
139998           NaN     4241.5              0.0  0.019841  
139999           NaN      666.5              0.0  0.019841  

[420000 rows x 18 columns]

# For fixed strike 10k

In [3]:
df_VOLCANIC_ROCK = get_product(df, 'VOLCANIC_ROCK')
df_VOLCANIC_ROCK_call_10000 = get_product(df, "VOLCANIC_ROCK_VOUCHER_10000")
df_VOLCANIC_ROCK_call_10000 = df_VOLCANIC_ROCK_call_10000.merge(df_VOLCANIC_ROCK[['timestamp', 'mid_price']], on='timestamp', suffixes=('', '_VOLCANIC_ROCK'))

In [4]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_VOLCANIC_ROCK['timestamp'], y=df_VOLCANIC_ROCK['mid_price'], name='VOLCANIC_ROCK Mid Price'))
fig.add_trace(go.Scatter(x=df_VOLCANIC_ROCK_call_10000['timestamp'], y=df_VOLCANIC_ROCK_call_10000['mid_price'], name='VOLCANIC_ROCK Call Mid Price', yaxis='y2'))
fig.update_layout(title='VOLCANIC_ROCK and VOLCANIC_ROCK Call Prices over Timestamp', yaxis=dict(title='VOLCANIC_ROCK Mid Price'), yaxis2=dict(title='VOLCANIC_ROCK Call Bid Price', overlaying='y', side='right'))
fig.show()


In [5]:
import numpy as np
from scipy.stats import norm
from scipy.optimize import brentq

def black_scholes_call(spot, strike, time_to_expiry, volatility):
    d1 = (np.log(spot / strike) + (0.5 * volatility ** 2) * time_to_expiry) / (volatility * np.sqrt(time_to_expiry))
    d2 = d1 - volatility * np.sqrt(time_to_expiry)
    call_price = (spot * norm.cdf(d1) - strike * norm.cdf(d2))
    return call_price

def black_scholes_put(spot, strike, time_to_expiry, volatility):
    d1 = (np.log(spot / strike) + (0.5 * volatility ** 2) * time_to_expiry) / (volatility * np.sqrt(time_to_expiry))
    d2 = d1 - volatility * np.sqrt(time_to_expiry)
    put_price = (strike * norm.cdf(-d2) - spot * norm.cdf(-d1))
    return put_price

def delta(spot, strike, time_to_expiry, volatility):
    d1 = (np.log(spot) - np.log(strike) + (0.5 * volatility ** 2) * time_to_expiry) / (volatility * np.sqrt(time_to_expiry))
    return norm.cdf(d1)

def gamma(spot, strike, time_to_expiry, volatility):
    d1 = (np.log(spot) - np.log(strike) + (0.5 * volatility ** 2) * time_to_expiry) / (volatility * np.sqrt(time_to_expiry))
    return norm.pdf(d1)/(spot * volatility * np.sqrt(time_to_expiry))

def vega(spot, strike, time_to_expiry, volatility):
    d1 = (np.log(spot) - np.log(strike) + (0.5 * volatility ** 2) * time_to_expiry) / (volatility * np.sqrt(time_to_expiry))
    return norm.pdf(d1) * (spot * np.sqrt(time_to_expiry)) / 100

def implied_volatility(call_price, spot, strike, time_to_expiry):
    # Define the equation where the root is the implied volatility
    def equation(volatility):
        estimated_price = black_scholes_call(spot, strike, time_to_expiry, volatility)
        return estimated_price - call_price

    # Using Brent's method to find the root of the equation
    implied_vol = brentq(equation, 1e-10, 3.0, xtol=1e-10)
    return implied_vol

def realized_vol(df_VOLCANIC_ROCK_call, window, step_size):
    df_VOLCANIC_ROCK_call[f'log_return_{step_size}'] = np.log(df_VOLCANIC_ROCK_call['mid_price_VOLCANIC_ROCK'].to_numpy()/df_VOLCANIC_ROCK_call['mid_price_VOLCANIC_ROCK'].shift(step_size).to_numpy())
    dt = step_size / 250 / 10000 
    df_VOLCANIC_ROCK_call[f'realized_vol_{step_size}'] = df_VOLCANIC_ROCK_call[f'log_return_{step_size}'].rolling(window=window).apply(lambda x: np.mean(x[::step_size]**2) / dt)
    df_VOLCANIC_ROCK_call[f'realized_vol_{step_size}'] = np.sqrt(df_VOLCANIC_ROCK_call[f'realized_vol_{step_size}'].to_numpy())
    return df_VOLCANIC_ROCK_call



In [6]:
df_VOLCANIC_ROCK_call_10000.head()

day  timestamp                      product  bid_price_1  bid_volume_1  \
0    0          0  VOLCANIC_ROCK_VOUCHER_10000        505.0          19.0   
1    0        100  VOLCANIC_ROCK_VOUCHER_10000        515.0          13.0   
2    0        200  VOLCANIC_ROCK_VOUCHER_10000        516.0          15.0   
3    0        300  VOLCANIC_ROCK_VOUCHER_10000        521.0          13.0   
4    0        400  VOLCANIC_ROCK_VOUCHER_10000        512.0          15.0   

   bid_price_2  bid_volume_2  bid_price_3  bid_volume_3  ask_price_1  \
0          NaN           NaN          NaN           NaN          506   
1          NaN           NaN          NaN           NaN          516   
2          NaN           NaN          NaN           NaN          517   
3          NaN           NaN          NaN           NaN          522   
4          NaN           NaN          NaN           NaN          513   

   ask_volume_1  ask_price_2  ask_volume_2  ask_price_3  ask_volume_3  \
0            19          NaN           NaN          NaN           NaN   
1            13          NaN           NaN          NaN           NaN   
2            15          NaN           NaN          NaN           NaN   
3            13          NaN           NaN          NaN           NaN   
4            15          NaN           NaN          NaN           NaN   

   mid_price  profit_and_loss    expiry  mid_price_VOLCANIC_ROCK  
0      505.5              0.0  0.027778                  10503.0  
1      515.5              0.0  0.027778                  10510.0  
2      516.5              0.0  0.027778                  10513.0  
3      521.5              0.0  0.027778                  10517.5  
4      512.5              0.0  0.027778                  10509.5

In [7]:
spot_price = 10000        # Spot price of the underlying asset
strike_price = 10000      # Strike price of the option
# call_price = 637.5         # Market price of the call option
time_to_expiry = 4/255      # Time to expiry in years
# initial_guess = 16

# try for 0th row
iv0 = implied_volatility(
    df_VOLCANIC_ROCK_call_10000.iloc[0]['mid_price'],
    df_VOLCANIC_ROCK_call_10000.iloc[0]['mid_price_VOLCANIC_ROCK'],
    strike_price,
    time_to_expiry=df_VOLCANIC_ROCK_call_10000.iloc[0]['expiry'],
)

print(f"Implied Volatility for 0th row: {iv0}")

# try for last row
iv_last = implied_volatility(
    df_VOLCANIC_ROCK_call_10000.iloc[-1]['mid_price'],
    df_VOLCANIC_ROCK_call_10000.iloc[-1]['mid_price_VOLCANIC_ROCK'],
    strike_price,
    time_to_expiry=df_VOLCANIC_ROCK_call_10000.iloc[-1]['expiry'],
)

print(f"Implied Volatility for last row: {iv_last}")

Implied Volatility for 0th row: 0.15099099787196868
Implied Volatility for last row: 0.11760315441510004


# Plot IV over time for fixed K=10k

In [8]:

df_VOLCANIC_ROCK_call_10000['implied_vol'] = df_VOLCANIC_ROCK_call_10000.apply(lambda row: implied_volatility(row['mid_price'], row['mid_price_VOLCANIC_ROCK'], strike_price, row['expiry']), axis=1)
fig = px.line(df_VOLCANIC_ROCK_call_10000, x='timestamp', y='implied_vol', title='Implied Volatility over Time, K = 10000')
fig.show()

In [9]:
df_VOLCANIC_ROCK_call_10000['delta'] = df_VOLCANIC_ROCK_call_10000.apply(lambda row: delta(row['mid_price_VOLCANIC_ROCK'], strike_price, row['expiry'], row['implied_vol']), axis=1)
df_VOLCANIC_ROCK_call_10000['gamma'] = df_VOLCANIC_ROCK_call_10000.apply(lambda row: gamma(row['mid_price_VOLCANIC_ROCK'], strike_price, row['expiry'], row['implied_vol']), axis=1)
df_VOLCANIC_ROCK_call_10000['vega'] = df_VOLCANIC_ROCK_call_10000.apply(lambda row: vega(row['mid_price_VOLCANIC_ROCK'], strike_price, row['expiry'], row['implied_vol']), axis=1)

In [10]:
import plotly.express as px

fig = px.line(df_VOLCANIC_ROCK_call_10000, x='timestamp', y='delta', title='Delta over Time')
fig.show()


In [11]:
fig = px.line(df_VOLCANIC_ROCK_call_10000, x='timestamp', y='vega', title='Vega over Time')
fig.show()

# Do different strikes

## K = 9500 (deep ITM)

In [27]:
df_VOLCANIC_ROCK_call_9500 = get_product(df, "VOLCANIC_ROCK_VOUCHER_9500")
df_VOLCANIC_ROCK_call_9500 = df_VOLCANIC_ROCK_call_9500.merge(df_VOLCANIC_ROCK[['timestamp', 'mid_price']], on='timestamp', suffixes=('', '_VOLCANIC_ROCK'))

An example of unsolvable IV: 

at timestamp = 4200 in day0: IV=0 would yield call_price=966.5, but market price is 966

In [42]:
row = df_VOLCANIC_ROCK_call_9500.query("timestamp == 4200").iloc[0] # extract as series
spot, strike, call_price, T = row['mid_price_VOLCANIC_ROCK'], 9500, row['mid_price'], row['expiry']
print(spot, strike, call_price)
black_scholes_call(spot, strike, T, volatility=1e-10)

10466.5 9500 966.0


966.5

In [32]:
underpriced_timestamps = []
up_dic = {} # store the underpriced timestamps

def safe_implied_vol(row):
    try:
        return implied_volatility(
            row['mid_price'], 
            row['mid_price_VOLCANIC_ROCK'], 
            9500, 
            row['expiry']
        )
    except Exception as e:
        underpriced_timestamps.append(row['timestamp'])
        # spot, strike, call_price, T
        up_dic[row['timestamp']] = (row['mid_price_VOLCANIC_ROCK'], 9500, row['mid_price'], row['expiry'])
        return np.nan

df_VOLCANIC_ROCK_call_9500['implied_vol'] = df_VOLCANIC_ROCK_call_9500.apply(safe_implied_vol, axis=1)

In [15]:
len(underpriced_timestamps), len(df_VOLCANIC_ROCK_call_9500)

(401, 30000)

In [43]:
fig = px.line(df_VOLCANIC_ROCK_call_9500, x='timestamp', y='implied_vol', title='Implied Vol over Time K=9500')
fig.show()

# note 402 timestamps have NaN, skipped by plt

In [44]:
df_VOLCANIC_ROCK_call_9500['delta'] = df_VOLCANIC_ROCK_call_9500.apply(lambda row: delta(row['mid_price_VOLCANIC_ROCK'], strike_price, row['expiry'], row['implied_vol']), axis=1)
df_VOLCANIC_ROCK_call_9500['gamma'] = df_VOLCANIC_ROCK_call_9500.apply(lambda row: gamma(row['mid_price_VOLCANIC_ROCK'], strike_price, row['expiry'], row['implied_vol']), axis=1)
df_VOLCANIC_ROCK_call_9500['vega'] = df_VOLCANIC_ROCK_call_9500.apply(lambda row: vega(row['mid_price_VOLCANIC_ROCK'], strike_price, row['expiry'], row['implied_vol']), axis=1)

# note again 402 timestamps have NaN, skipped by plt
fig = px.line(df_VOLCANIC_ROCK_call_9500, x='timestamp', y='delta', title='Delta over Time K=9500')
fig.show()

# K = 9750 (Slightly ITM)

In [51]:
df_VOLCANIC_ROCK_call_9750 = get_product(df, "VOLCANIC_ROCK_VOUCHER_9750")
df_VOLCANIC_ROCK_call_9750 = df_VOLCANIC_ROCK_call_9750.merge(df_VOLCANIC_ROCK[['timestamp', 'mid_price']], on='timestamp', suffixes=('', '_VOLCANIC_ROCK'))
underpriced_timestamps_9750 = []
up_dic_9750 = {} # store the underpriced timestamps

def safe_implied_vol(row):
    try:
        return implied_volatility(
            row['mid_price'], 
            row['mid_price_VOLCANIC_ROCK'], 
            9750,
            row['expiry']
        )
    except Exception as e:
        underpriced_timestamps_9750.append(row['timestamp'])
        # spot, strike, call_price, T
        up_dic_9750[row['timestamp']] = (row['mid_price_VOLCANIC_ROCK'], 9750, row['mid_price'], row['expiry'])
        return np.nan

df_VOLCANIC_ROCK_call_9750['implied_vol'] = df_VOLCANIC_ROCK_call_9750.apply(safe_implied_vol, axis=1)

In [52]:
len(underpriced_timestamps_9750), len(df_VOLCANIC_ROCK_call_9750)

(52, 30000)

In [53]:
fig = px.line(df_VOLCANIC_ROCK_call_9750, x='timestamp', y='implied_vol', title='Implied Vol over Time K=9750')
fig.show()

## K= 10500 （Deep OTM)

In [45]:
df_VOLCANIC_ROCK_call_10500 = get_product(df, "VOLCANIC_ROCK_VOUCHER_10500")
df_VOLCANIC_ROCK_call_10500 = df_VOLCANIC_ROCK_call_10500.merge(df_VOLCANIC_ROCK[['timestamp', 'mid_price']], on='timestamp', suffixes=('', '_VOLCANIC_ROCK'))
df_VOLCANIC_ROCK_call_10500['implied_vol'] = df_VOLCANIC_ROCK_call_10500.apply(lambda row: implied_volatility(row['mid_price'], row['mid_price_VOLCANIC_ROCK'], 10500, row['expiry']), axis=1)
fig = px.line(df_VOLCANIC_ROCK_call_10500, x='timestamp', y='implied_vol', title='Implied Vol over Time K=10500')
fig.show()

# K = 10250 slightly OTM

In [47]:
df_VOLCANIC_ROCK_call_10250 = get_product(df, "VOLCANIC_ROCK_VOUCHER_10250")
df_VOLCANIC_ROCK_call_10250 = df_VOLCANIC_ROCK_call_10250.merge(df_VOLCANIC_ROCK[['timestamp', 'mid_price']], on='timestamp', suffixes=('', '_VOLCANIC_ROCK'))
df_VOLCANIC_ROCK_call_10250['implied_vol'] = df_VOLCANIC_ROCK_call_10250.apply(lambda row: implied_volatility(row['mid_price'], row['mid_price_VOLCANIC_ROCK'], 10250, row['expiry']), axis=1)
fig = px.line(df_VOLCANIC_ROCK_call_10250, x='timestamp', y='implied_vol', title='Implied Vol over Time K=10250')
fig.show()

# backtest strat-trading implied volatility to mean

In [54]:
df_backtest = df_VOLCANIC_ROCK_call_10000[['timestamp', 'mid_price', 'mid_price_VOLCANIC_ROCK', 'implied_vol', 'delta', 'vega']]
df_backtest = df_backtest.rename(columns={'mid_price': 'mid_price_VOUCHER'})
df_backtest['implied_vol'].mean()

0.14191289318001687

In [55]:
implied_vol_mean = 0.15

In [56]:
import pandas as pd

# Set the threshold values
upper_threshold = 0.006  # Threshold for selling option
lower_threshold = -0.006  # Threshold for buying option
close_threshold = 0.0001  # Threshold for clearing position

# Initialize variables
position = 0
pnl = 0
vega_pnl = 0
trade_history = []

# Iterate over each row in the dataframe
for idx, row in df_backtest.iterrows():
    implied_vol = row['implied_vol']
    if idx == 0:
        continue
    prev_implied_vol = df_backtest.iloc[idx-1]['implied_vol']
    mid_price_VOUCHER = row['mid_price_VOUCHER']
    mid_price_VOLCANIC_ROCK = row['mid_price_VOLCANIC_ROCK']
    vega = row['vega']
    d = row['delta']

    # Check if implied vol is above the upper threshold and no current position
    if implied_vol > implied_vol_mean + upper_threshold and position == 0:
        # Sell 1 delta hedged option
        position = -1
        entry_price_VOUCHER = mid_price_VOUCHER
        entry_price_VOLCANIC_ROCK = mid_price_VOLCANIC_ROCK
        trade_history.append((-1, entry_price_VOUCHER, entry_price_VOLCANIC_ROCK, implied_vol))

    # Check if implied vol is below the lower threshold and no current position
    elif implied_vol < implied_vol_mean + lower_threshold and position == 0:
        # Buy 1 delta hedged option
        position = 1
        entry_price_VOUCHER = mid_price_VOUCHER
        entry_price_VOLCANIC_ROCK = mid_price_VOLCANIC_ROCK
        trade_history.append((1, entry_price_VOUCHER, entry_price_VOLCANIC_ROCK, implied_vol))

    # Check if implied vol is within the close threshold and there is a current position
    elif abs(implied_vol - implied_vol_mean) <= close_threshold and position != 0:
        # Clear the position (option_pos - delta * stock_pos)
        pnl += position * (mid_price_VOUCHER - entry_price_VOUCHER + d * (entry_price_VOLCANIC_ROCK - mid_price_VOLCANIC_ROCK))
        position = 0
        trade_history.append((0, mid_price_VOUCHER, mid_price_VOLCANIC_ROCK, implied_vol))

    if position != 0:
        vega_pnl += position * vega * (implied_vol - prev_implied_vol) * 100
# Calculate final PnL if there is still an open position
if position != 0:
    pnl += position * (mid_price_VOUCHER - entry_price_VOUCHER + d * (entry_price_VOLCANIC_ROCK - mid_price_VOLCANIC_ROCK))

# Print the trade history and final PnL
print("Trade History:")
for trade in trade_history:
    print(f"Position: {trade[0]}, Option Price: {trade[1]}, Underlying Price: {trade[2]}, Implied Volatility: {trade[3]}")

print(f"\nFinal PnL: {pnl}")

Trade History:
Position: -1, Option Price: 515.5, Underlying Price: 10510.0, Implied Volatility: 0.17565155105349467
Position: 0, Option Price: 483.5, Underlying Price: 10480.5, Implied Volatility: 0.14999468339426164
Position: -1, Option Price: 479.5, Underlying Price: 10475.0, Implied Volatility: 0.1598541538628892
Position: 0, Option Price: 431.5, Underlying Price: 10426.5, Implied Volatility: 0.14992331507920703
Position: 1, Option Price: 427.0, Underlying Price: 10423.0, Implied Volatility: 0.14266122075488927
Position: 0, Option Price: 412.5, Underlying Price: 10406.5, Implied Volatility: 0.14992660886197257
Position: 1, Option Price: 409.5, Underlying Price: 10405.0, Implied Volatility: 0.14101316508313388
Position: 0, Option Price: 454.5, Underlying Price: 10450.5, Implied Volatility: 0.14995731877890314
Position: -1, Option Price: 446.5, Underlying Price: 10440.5, Implied Volatility: 0.1595097096227288
Position: 0, Option Price: 432.0, Underlying Price: 10427.0, Implied Volati

In [57]:
pnl, vega_pnl

(211.31001044792146, 845.211443829884)

In [58]:
import pandas as pd

# Set the threshold values
upper_threshold = 0.005  # Threshold for selling option
lower_threshold = -0.005  # Threshold for buying option

# Initialize variables
position = 0
pnl = 0
trade_history = []

# Iterate over each row in the dataframe
for _, row in df_backtest.iterrows():
    implied_vol = row['implied_vol']
    mid_price_VOUCHER = row['mid_price_VOUCHER']
    mid_price_VOLCANIC_ROCK = row['mid_price_VOLCANIC_ROCK']
    d = row['delta']

    # Check if implied vol is above the upper threshold
    if implied_vol > implied_vol_mean + upper_threshold:
        # Sell to target position of -1
        if position > -1:
            quantity = -1 - position
            position = -1
            entry_price_VOUCHER = mid_price_VOUCHER
            entry_price_VOLCANIC_ROCK = mid_price_VOLCANIC_ROCK
            trade_history.append((quantity, entry_price_VOUCHER, entry_price_VOLCANIC_ROCK, implied_vol))

    # Check if implied vol is below the lower threshold
    elif implied_vol < implied_vol_mean + lower_threshold:
        # Buy to target position of 1
        if position < 1:
            quantity = 1 - position
            position = 1
            entry_price_VOUCHER = mid_price_VOUCHER
            entry_price_VOLCANIC_ROCK = mid_price_VOLCANIC_ROCK
            trade_history.append((quantity, entry_price_VOUCHER, entry_price_VOLCANIC_ROCK, implied_vol))

# Calculate final PnL for the remaining position
if position != 0:
    pnl += position * (mid_price_VOUCHER - entry_price_VOUCHER + d * (entry_price_VOLCANIC_ROCK - mid_price_VOLCANIC_ROCK))

# Print the trade history and final PnL
print("Trade History:")
for trade in trade_history:
    print(f"Quantity: {trade[0]}, Option Price: {trade[1]}, Underlying Price: {trade[2]}, Implied Volatility: {trade[3]}")

print(f"\nFinal PnL: {pnl}")

Trade History:
Quantity: -1, Option Price: 515.5, Underlying Price: 10510.0, Implied Volatility: 0.17565155105349467
Quantity: 2, Option Price: 426.5, Underlying Price: 10422.5, Implied Volatility: 0.14252780094121745
Quantity: -2, Option Price: 437.5, Underlying Price: 10431.5, Implied Volatility: 0.15698682937997321
Quantity: 2, Option Price: 446.5, Underlying Price: 10443.0, Implied Volatility: 0.14439322626316953
Quantity: -2, Option Price: 449.5, Underlying Price: 10444.0, Implied Volatility: 0.15767109488253678
Quantity: 2, Option Price: 432.5, Underlying Price: 10428.5, Implied Volatility: 0.1441270066257974
Quantity: -2, Option Price: 441.5, Underlying Price: 10436.0, Implied Volatility: 0.15545909603427013
Quantity: 2, Option Price: 434.5, Underlying Price: 10431.0, Implied Volatility: 0.1412644488764526
Quantity: -2, Option Price: 416.5, Underlying Price: 10409.5, Implied Volatility: 0.1558398819025781
Quantity: 2, Option Price: 441.5, Underlying Price: 10438.0, Implied Volat